In [67]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Data Extraction
We are provided with the SQL Lite data containing a dataset from NWCG from year 1992-2015. In this particular step we are trying to:-
1. Extract Data from SQL Lite database
2. Filtering out data for California
3. Grouping data based on county and seeing which county had the most fire incidents
4. This will help us to narrow down to 1 county to start our work with.

In [68]:
# Importing data from SQL Lite to Pandas Dataframe
import sqlite3
cnx = sqlite3.connect('./FPA_FOD_20170508.sqlite')
df = pd.read_sql_query("SELECT * FROM fires", cnx)


In [69]:
# Seeing the sample data
df.head(4)

OBJECTID  FOD_ID      FPA_ID SOURCE_SYSTEM_TYPE SOURCE_SYSTEM  \
0         1       1  FS-1418826                FED   FS-FIRESTAT   
1         2       2  FS-1418827                FED   FS-FIRESTAT   
2         3       3  FS-1418835                FED   FS-FIRESTAT   
3         4       4  FS-1418845                FED   FS-FIRESTAT   

  NWCG_REPORTING_AGENCY NWCG_REPORTING_UNIT_ID  NWCG_REPORTING_UNIT_NAME  \
0                    FS                USCAPNF    Plumas National Forest   
1                    FS                USCAENF  Eldorado National Forest   
2                    FS                USCAENF  Eldorado National Forest   
3                    FS                USCAENF  Eldorado National Forest   

  SOURCE_REPORTING_UNIT SOURCE_REPORTING_UNIT_NAME  ... FIRE_SIZE_CLASS  \
0                  0511     Plumas National Forest  ...               A   
1                  0503   Eldorado National Forest  ...               A   
2                  0503   Eldorado National Forest  ...               A   
3                  0503   Eldorado National Forest  ...               A   

    LATITUDE   LONGITUDE OWNER_CODE       OWNER_DESCR STATE COUNTY FIPS_CODE  \
0  40.036944 -121.005833        5.0              USFS    CA     63       063   
1  38.933056 -120.404444        5.0              USFS    CA     61       061   
2  38.984167 -120.735556       13.0  STATE OR PRIVATE    CA     17       017   
3  38.559167 -119.913333        5.0              USFS    CA      3       003   

   FIPS_NAME                                              Shape  
0     Plumas  b'\x00\x01\xad\x10\x00\x00\xe8d\xc2\x92_@^\xc0...  
1     Placer  b'\x00\x01\xad\x10\x00\x00T\xb6\xeej\xe2\x19^\...  
2  El Dorado  b'\x00\x01\xad\x10\x00\x00\xd0\xa5\xa0W\x13/^\...  
3     Alpine  b'\x00\x01\xad\x10\x00\x00\x94\xac\xa3\rt\xfa]...  

[4 rows x 39 columns]

In [70]:
# Checking the infor about the data frame
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1880465 entries, 0 to 1880464
Data columns (total 39 columns):
 #   Column                      Dtype  
---  ------                      -----  
 0   OBJECTID                    int64  
 1   FOD_ID                      int64  
 2   FPA_ID                      object 
 3   SOURCE_SYSTEM_TYPE          object 
 4   SOURCE_SYSTEM               object 
 5   NWCG_REPORTING_AGENCY       object 
 6   NWCG_REPORTING_UNIT_ID      object 
 7   NWCG_REPORTING_UNIT_NAME    object 
 8   SOURCE_REPORTING_UNIT       object 
 9   SOURCE_REPORTING_UNIT_NAME  object 
 10  LOCAL_FIRE_REPORT_ID        object 
 11  LOCAL_INCIDENT_ID           object 
 12  FIRE_CODE                   object 
 13  FIRE_NAME                   object 
 14  ICS_209_INCIDENT_NUMBER     object 
 15  ICS_209_NAME                object 
 16  MTBS_ID                     object 
 17  MTBS_FIRE_NAME              object 
 18  COMPLEX_NAME                object 
 19  FIRE_YEAR            

In [71]:
df.OBJECTID.count()

1880465

We can see here that we are having 1880464 data records

**Filtering data with respect to CA**

From the below mentioned max count it is pretty evident that california has the maximum number of fire event.

### Conclusion of the Data Extraction
As we have seen from above that the state with most number of fire is california then lets pull this data out from the dataframe and get the list of all the CA records.

In [72]:
# California Wild Fire incident dataset is stores in the file 'California_Forest_Fire_Data.csv'
dfCali = df.loc[df.STATE == "CA"]
print(dfCali.STATE.count())
dfCali.to_csv('California_Forest_Fire_Data.csv', index=False)

189550


### In this section we will try to narrow down the California wildfire data in order to figure out a county that has the most number of wildfire in all these year

In [73]:
# Inspecting the data for California
dfCali.head()

OBJECTID  FOD_ID      FPA_ID SOURCE_SYSTEM_TYPE SOURCE_SYSTEM  \
0         1       1  FS-1418826                FED   FS-FIRESTAT   
1         2       2  FS-1418827                FED   FS-FIRESTAT   
2         3       3  FS-1418835                FED   FS-FIRESTAT   
3         4       4  FS-1418845                FED   FS-FIRESTAT   
4         5       5  FS-1418847                FED   FS-FIRESTAT   

  NWCG_REPORTING_AGENCY NWCG_REPORTING_UNIT_ID  NWCG_REPORTING_UNIT_NAME  \
0                    FS                USCAPNF    Plumas National Forest   
1                    FS                USCAENF  Eldorado National Forest   
2                    FS                USCAENF  Eldorado National Forest   
3                    FS                USCAENF  Eldorado National Forest   
4                    FS                USCAENF  Eldorado National Forest   

  SOURCE_REPORTING_UNIT SOURCE_REPORTING_UNIT_NAME  ... FIRE_SIZE_CLASS  \
0                  0511     Plumas National Forest  ...               A   
1                  0503   Eldorado National Forest  ...               A   
2                  0503   Eldorado National Forest  ...               A   
3                  0503   Eldorado National Forest  ...               A   
4                  0503   Eldorado National Forest  ...               A   

    LATITUDE   LONGITUDE OWNER_CODE       OWNER_DESCR STATE COUNTY FIPS_CODE  \
0  40.036944 -121.005833        5.0              USFS    CA     63       063   
1  38.933056 -120.404444        5.0              USFS    CA     61       061   
2  38.984167 -120.735556       13.0  STATE OR PRIVATE    CA     17       017   
3  38.559167 -119.913333        5.0              USFS    CA      3       003   
4  38.559167 -119.933056        5.0              USFS    CA      3       003   

   FIPS_NAME                                              Shape  
0     Plumas  b'\x00\x01\xad\x10\x00\x00\xe8d\xc2\x92_@^\xc0...  
1     Placer  b'\x00\x01\xad\x10\x00\x00T\xb6\xeej\xe2\x19^\...  
2  El Dorado  b'\x00\x01\xad\x10\x00\x00\xd0\xa5\xa0W\x13/^\...  
3     Alpine  b'\x00\x01\xad\x10\x00\x00\x94\xac\xa3\rt\xfa]...  
4     Alpine  b'\x00\x01\xad\x10\x00\x00@\xe3\xaa.\xb7\xfb]\...  

[5 rows x 39 columns]

In [74]:
# Checking the various data types California Data Frame has
dfCali.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 189550 entries, 0 to 1880464
Data columns (total 39 columns):
 #   Column                      Non-Null Count   Dtype  
---  ------                      --------------   -----  
 0   OBJECTID                    189550 non-null  int64  
 1   FOD_ID                      189550 non-null  int64  
 2   FPA_ID                      189550 non-null  object 
 3   SOURCE_SYSTEM_TYPE          189550 non-null  object 
 4   SOURCE_SYSTEM               189550 non-null  object 
 5   NWCG_REPORTING_AGENCY       189550 non-null  object 
 6   NWCG_REPORTING_UNIT_ID      189550 non-null  object 
 7   NWCG_REPORTING_UNIT_NAME    189550 non-null  object 
 8   SOURCE_REPORTING_UNIT       189550 non-null  object 
 9   SOURCE_REPORTING_UNIT_NAME  189550 non-null  object 
 10  LOCAL_FIRE_REPORT_ID        61933 non-null   object 
 11  LOCAL_INCIDENT_ID           127983 non-null  object 
 12  FIRE_CODE                   55533 non-null   object 
 13  FIRE_NAME    

In [75]:
# Checking the dataframe for null values
dfCali.isnull().sum()

OBJECTID                           0
FOD_ID                             0
FPA_ID                             0
SOURCE_SYSTEM_TYPE                 0
SOURCE_SYSTEM                      0
NWCG_REPORTING_AGENCY              0
NWCG_REPORTING_UNIT_ID             0
NWCG_REPORTING_UNIT_NAME           0
SOURCE_REPORTING_UNIT              0
SOURCE_REPORTING_UNIT_NAME         0
LOCAL_FIRE_REPORT_ID          127617
LOCAL_INCIDENT_ID              61567
FIRE_CODE                     134017
FIRE_NAME                      14993
ICS_209_INCIDENT_NUMBER       186712
ICS_209_NAME                  186712
MTBS_ID                       188413
MTBS_FIRE_NAME                188413
COMPLEX_NAME                  188623
FIRE_YEAR                          0
DISCOVERY_DATE                     0
DISCOVERY_DOY                      0
DISCOVERY_TIME                 79333
STAT_CAUSE_CODE                    0
STAT_CAUSE_DESCR                   0
CONT_DATE                      97642
CONT_DOY                       97642
C

We observe that there is no null data in latitude and longitude. All the data frames with respect to latitude and longitude are filled. We also see that there are certain counties that are missing. Lets use the Latitude and Longitude data to fill all the County Information.

### Generating County information as per Latitude and Longitude using Geopy package

In [76]:
# importing Geopy with functools
from geopy.geocoders import ArcGIS
from geopy.extra.rate_limiter import RateLimiter
import json

# Creating a geolocator variable with dummy app name
geolocator = ArcGIS()
reverse = RateLimiter(geolocator.reverse)

# Reverse query in order to check whether its working fine or not
county = reverse(("37.3337, -121.8907"), exactly_one=True).raw
county['Subregion']

'Santa Clara County'

In [77]:
# Method generating county name using the latitude and longitude data.
def getCountyInfo(lat_lang_str):
    try:
        return reverse((lat_lang_str), exactly_one=True).raw
    except:
        pass

In [82]:
# county_geocode_list = []
# dfCaliCountyNull = dfCali[dfCali.COUNTY.isnull()]
# count = 0
# for index,row in dfCaliCountyNull.iterrows():
#     if count % 1000 == 0:
#         with open(str(count)+'countyData.json', 'w') as f:
#             json.dump(county_geocode_list, f)
#     latitude = repr(row['LATITUDE'])
#     longitude = repr(row['LONGITUDE'])
#     geoData = getCountyInfo(latitude+","+longitude)
#     geoData['Latitude'] = latitude;
#     geoData['Longitude'] = longitude;
#     county_geocode_list.append(geoData)
#     count = count+1
#     print(index)
dfCali['NewCountyValue'] = None

for index,row in dfCali.iterrows():
    try:
        latitude = repr(row['LATITUDE'])
        longitude = repr(row['LONGITUDE'])
        geoData = getCountyInfo(latitude+","+longitude)
        geoData['Latitude'] = latitude
        geoData['Longitude'] = longitude
        dfCali.at[index, 'NewCountyValue']=geoData['Subregion']
        print(dfCali['NewCountyValue'][index])
        print(index)
    except:
        print('Exception found')
        continue

<ipython-input-82-52ebe520d227>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfCali['NewCountyValue'] = None


Plumas County
0
El Dorado County
1
El Dorado County
2
Alpine County
3
Alpine County
4
Amador County
5
El Dorado County
6
Shasta County
7
Siskiyou County
8
Amador County
9
El Dorado County
10
Amador County
11
El Dorado County
12
Calaveras County
13
El Dorado County
14
El Dorado County
15
Amador County
16
El Dorado County
17
El Dorado County
18
Humboldt County
76
Los Angeles County
87
Los Angeles County
88
El Dorado County
90
Alpine County
95
Mono County
96
Riverside County
105
Mono County
106
Riverside County
109
Fresno County
110
Alpine County
132
Kern County
146
Mono County
149
Mono County
152
Kern County
154
Monterey County
155
Monterey County
156
Monterey County
157
Mono County
158
Mono County
159
Mono County
160
Mono County
163
Mono County
164
Tuolumne County
170
Alpine County
171
Santa Barbara County
177
San Luis Obispo County
178
Kern County
179
Santa Barbara County
180
Monterey County
181
Monterey County
182
Ventura County
183
Kern County
203
Kern County
207
Kern County
210
Kern

Tuolumne County
3587
Lassen County
3600
Tuolumne County
3602
Modoc County
3603
Modoc County
3608
Modoc County
3619
San Diego County
3626

3630
Modoc County
3640
Modoc County
3646
Modoc County
3651
Tuolumne County
3663
Los Angeles County
3668
Calaveras County
3673
Los Angeles County
3680
Lassen County
3682
Los Angeles County
3685
Los Angeles County
3688
Los Angeles County
3692
Los Angeles County
3696
Lassen County
3703
Los Angeles County
3707
Tuolumne County
3708
Los Angeles County
3710
Los Angeles County
3713
Los Angeles County
3718
San Bernardino County
3722
Tuolumne County
3726
Los Angeles County
3729
Lassen County
3730
Los Angeles County
3731
Los Angeles County
3733
Los Angeles County
3734
Los Angeles County
3735
Los Angeles County
3736
Modoc County
3737
Los Angeles County
3738
Los Angeles County
3739
Los Angeles County
3740
Los Angeles County
3741
Monterey County
3743
Los Angeles County
3744
Los Angeles County
3745
Los Angeles County
3746
San Bernardino County
3747
Los Angeles Coun

Los Angeles County
5378
Los Angeles County
5380
Los Angeles County
5385
Los Angeles County
5386
Los Angeles County
5388
Los Angeles County
5392
Los Angeles County
5394
Los Angeles County
5396
Los Angeles County
5400
Lake County
5416
Lake County
5423
Siskiyou County
5425
Lake County
5430
Lake County
5440
Humboldt County
5458
Humboldt County
5465
Humboldt County
5469
Trinity County
5470
El Dorado County
5481
Nevada County
5646
Sierra County
5668
Riverside County
5940
Riverside County
5951
Orange County
5956
Riverside County
5969
Riverside County
5974
Riverside County
5976
El Dorado County
5987
Los Angeles County
5991
El Dorado County
5992
El Dorado County
5994
Amador County
6000
El Dorado County
6002
Calaveras County
6004
El Dorado County
6007
Trinity County
6027
San Diego County
6040
Los Angeles County
6057
Trinity County
6062
Siskiyou County
6064
Los Angeles County
6090
Los Angeles County
6092
Los Angeles County
6098
Los Angeles County
6105
Los Angeles County
6109
Trinity County
6111
L

Sierra County
8688
Plumas County
8689
Sierra County
8690
Plumas County
8691
Nevada County
8692
Sierra County
8693
Alpine County
8694
Alpine County
8695
Plumas County
8696
Plumas County
8698
Alpine County
8699
Plumas County
8700
Alpine County
8716
Plumas County
8725
Plumas County
8726
Fresno County
8727
Fresno County
8728
Fresno County
8729
Fresno County
8730
Los Angeles County
8731
Los Angeles County
8732
Alpine County
8734
Alpine County
8740
Mono County
8742
Alpine County
8744
Sierra County
8756
Plumas County
8758
Plumas County
8760
Trinity County
8765
Mono County
8769
Alpine County
8770
Alpine County
8776
Lassen County
8783
Lassen County
8786
Lassen County
8788
Lassen County
8789
Lassen County
8791
Lassen County
8792
Los Angeles County
8797
Sierra County
8808
Plumas County
8810
Plumas County
8812
Placer County
8817
Lassen County
8822
Alpine County
8831
Lassen County
8833
Tehama County
8836
Siskiyou County
8837
Siskiyou County
8838
Siskiyou County
8853
Siskiyou County
8862
Shasta Coun

...

Nevada County
1878931
Butte County
1878932
Butte County
1878933
Merced County
1878934
Tulare County
1878935
Contra Costa County
1878936
San Diego County
1878937
San Diego County
1878938
Fresno County
1878939
San Diego County
1878940
Mendocino County
1878941
Kern County
1878942
Fresno County
1878943
Ventura County
1878944
Sonoma County
1878945
Mendocino County
1878946
Siskiyou County
1878947
Mendocino County
1878948
Tulare County
1878949
Los Angeles County
1878950
San Mateo County
1878951
Sonoma County
1878952
Nevada County
1878953
Humboldt County
1878954
Madera County
1878955
Contra Costa County
1878956
El Dorado County
1878957
Tulare County
1878958
Kern County
1878959
Calaveras County
1878960
Napa County
1878961
El Dorado County
1878962
Santa Cruz County
1878963
Placer County
1878964
Butte County
1878965
Tuolumne County
1878966
Riverside County
1878967
Alameda County
1878968
Napa County
1878969
Amador County
1878970
Napa County
1878971
Napa County
1878972
Del Norte County
1878973
Fres

Tuolumne County
1879278
Tuolumne County
1879279
San Bernardino County
1879280
Shasta County
1879281
Shasta County
1879282
San Bernardino County
1879283
Fresno County
1879284
Yuba County
1879285
Sonoma County
1879286
San Luis Obispo County
1879287
San Luis Obispo County
1879288
Nevada County
1879289
Riverside County
1879290
Contra Costa County
1879291
Tuolumne County
1879292
Butte County
1879293
San Luis Obispo County
1879294
Sacramento County
1879295
San Luis Obispo County
1879296
El Dorado County
1879297
San Luis Obispo County
1879298
Mendocino County
1879299
Riverside County
1879300
Marin County
1879301
Yolo County
1879302
Siskiyou County
1879303
Lassen County
1879304
Shasta County
1879305
Trinity County
1879306
Kern County
1879307
Santa Clara County
1879308
Sonoma County
1879309
Santa Barbara County
1879310
Ventura County
1879311
Lake County
1879312
Yolo County
1879313
Marin County
1879314
Lake County
1879315
Madera County
1879316
Ventura County
1879317
Stanislaus County
1879318
But

Placer County
1879626
Riverside County
1879627
Alameda County
1879628
Calaveras County
1879629
El Dorado County
1879630
Napa County
1879631
Sonoma County
1879632
Sonoma County
1879633
Shasta County
1879634
El Dorado County
1879635
Shasta County
1879636
Mendocino County
1879637
Napa County
1879638
Riverside County
1879639
El Dorado County
1879640
Amador County
1879641
El Dorado County
1879642
San Bernardino County
1879643
Fresno County
1879644
Sonoma County
1879645
Inyo County
1879646
Amador County
1879647
Tehama County
1879648
El Dorado County
1879649
Lake County
1879650
San Luis Obispo County
1879651
Butte County
1879652
Humboldt County
1879653
Humboldt County
1879654
Tuolumne County
1879655
Shasta County
1879656
San Joaquin County
1879657
Sonoma County
1879658
Los Angeles County
1879659
Mendocino County
1879660
Butte County
1879661
Riverside County
1879662
Monterey County
1879663
Monterey County
1879664
Siskiyou County
1879665
Monterey County
1879666
Nevada County
1879667
Siskiyou Co

El Dorado County
1879974
Butte County
1879975
San Bernardino County
1879976
Mendocino County
1879977
Sonoma County
1879978
Lake County
1879979
San Diego County
1879980
Riverside County
1879981
Tehama County
1879982
Tulare County
1879983
Sonoma County
1879984
San Diego County
1879985
Fresno County
1879986
Merced County
1879987
Merced County
1879988
Mariposa County
1879989
Lassen County
1879990
Tehama County
1879991
Riverside County
1879992
Trinity County
1879993
Riverside County
1879994
Riverside County
1879995
Riverside County
1879996
Shasta County
1879997
Shasta County
1879998
Calaveras County
1879999
Tulare County
1880000
Shasta County
1880001
Tulare County
1880002
Santa Cruz County
1880003
San Luis Obispo County
1880004
Humboldt County
1880005
Stanislaus County
1880006
Calaveras County
1880007
Tulare County
1880008
Tulare County
1880009
Humboldt County
1880010
Sonoma County
1880011
San Luis Obispo County
1880012
Calaveras County
1880013
San Diego County
1880014
Humboldt County
18800

Nevada County
1880319
San Bernardino County
1880320
Del Norte County
1880321
Monterey County
1880322
Mariposa County
1880323
Fresno County
1880324
Alameda County
1880325
Kern County
1880326
Shasta County
1880327
Santa Clara County
1880328
Tuolumne County
1880329
Tulare County
1880330
Butte County
1880331
Madera County
1880332
Butte County
1880333
Butte County
1880334
Sonoma County
1880335
Sonoma County
1880336
Shasta County
1880337
Madera County
1880338
Lassen County
1880339
Trinity County
1880340
Tijuana
1880341
Lassen County
1880342
Placer County
1880343
Shasta County
1880344
Napa County
1880345
Butte County
1880346
Placer County
1880347
Placer County
1880348
San Joaquin County
1880349
Placer County
1880350
Shasta County
1880351
Contra Costa County
1880352
El Dorado County
1880353
Alameda County
1880354
Stanislaus County
1880355
Shasta County
1880356
San Bernardino County
1880357
Merced County
1880358
Placer County
1880359
Contra Costa County
1880360
Placer County
1880361
Lassen Coun

In [83]:
dfCali.to_csv('FinalCaliData.csv', index=False)